In [132]:
import json
from langchain.chains.question_answering import load_qa_chain
from langchain.llms import OpenAI
from langchain.chat_models import ChatOpenAI
from dotenv import load_dotenv, find_dotenv
import os
import openai
import traceback
from tqdm import tqdm

from langchain.prompts.chat import (
    ChatPromptTemplate,
    HumanMessagePromptTemplate,
    SystemMessagePromptTemplate,
)

In [2]:
load_dotenv(find_dotenv(), override=True)

True

In [3]:
with open('reviews_output.json', 'r') as f:
    data = json.load(f)

In [11]:
model_version = "gpt-4-1106-preview"
chat_llm=ChatOpenAI(temperature=0, model_name=model_version)

In [46]:
def request_chat(messages):
    try:
        response = openai.chat.completions.create(
            model='gpt-4-1106-preview',
            messages=messages,
            response_format={ "type": "json_object" }
        )
    
        return response
    except openai.APIError as e:
        # Handle API error here, e.g. retry or log
        print(f"OpenAI API returned an API Error: {e}")
    
    except openai.AuthenticationError as e:
        # Handle Authentication error here, e.g. invalid API key
        print(f"OpenAI API returned an Authentication Error: {e}")
    
    except openai.APIConnectionError as e:
        # Handle connection error here
        print(f"Failed to connect to OpenAI API: {e}")
    
    
    except Exception as e:
        # Handles all other exceptions
        print(e)

In [119]:
def request(reviews_data):
    system_prompt = "You are a helpful assistant that finds reviews that are relevant to the restaurant."
    human_prompt = """
Given a restaurant's reviews and their IDs below, find 10 positive reviews and 10 negative reviews regarding each of the topics listed below:
1. Service
2. Hygiene and environment
3. Food quality and taste
4. Location and transportation
5. Price
When returning the results, include a score from 5 to 10 based on the reviews put the reviews that have strong opinions in the front and make sure to include the IDs of the reviews with the json format below:
{
    Category: {
        "Score": score
        "Positive": {'ID: review'}
        "Negative": {'ID: review'}
    }
}
========
Following is the example response, do not include them in the actual answer!
EXAMPLE ANSWER:
{
"Services": {
    "Score": 8.3,
    "Positive": {
        3: "The service is superb!",
        4: "The waiters are very well trained."
    },
    "Negative": {
        10: "The owner's attitude is the worst!",
        15: "The waiters need some training."
    }
},
"Hygiene and environment": {
    "Score": 7.1,
    "Positive": {
        20: "The environment is superb!",
        24: "The restaurant is very well cleaned."
    },
    "Negative": {
        30: "The hygiene is the worst!",
        36: "Some of the plates are clearly not washed."
    }
},
"Food quality and taste": {
    "Score": 5.0,
    "Positive": {
        47: "The food here is exceptional!"
    },
    "Negative": {
        49: "The taste is awful!"
    }
},
"Location and transportation": {
    "Score": 7.4,
    "Positive": {
        51: "There is good parking here."
    },
    "Negative": {
        52: "This place is so hard to get to."
    }
},
"Price": {
    "Score": 9.0,
    "Positive": {
        1: "The food is superb for this price!"
    },
    "Negative": {
        11: "Food here is so expensive!"
    }
} 

========
Reveiws:
"""
    for x in reviews_data:
        human_prompt += str(x['id']) + ": " + x['text'] + '\n'
    human_prompt += """========
DO NOT make up answers. Return the reviews as they are provided and do not include reviews in the example response!
ANSWER:
"""
    messages = [
            {"role": "system", "content": system_prompt},
            {"role": "user", "content": human_prompt}
    ]
    result = request_chat(messages)
    return result

res = request(data)
print(res)

ChatCompletion(id='chatcmpl-8MMmxt5dNouC71Mm0nl1CDRVQkRjL', choices=[Choice(finish_reason='stop', index=0, message=ChatCompletionMessage(content='{\n    "Service": {\n        "Score": 6,\n        "Positive": {\n            "3": "The place is cute and the staff was very friendly. Nice menu. Good for brunch.",\n            "8": "I went on a Thursday morning for breakfast. Staff was attentive and the omelette was excellent.",\n            "17": "This place is delicious. I love the vanilla chai tea latte they have, the manager is very hands-on and really seems to really know the business.",\n            "35": "The manager noticed and got me my check and packed my leftovers asap.",\n            "37": "The server couldn\'t have been more attentive and friendly.",\n            "51": "Great French press coffee and the staff is really working hard.",\n            "60": "Fantastic meal! We didn\'t have to wait long and the service was spot on.",\n            "61": "Our waitress was extremely nic

In [120]:
result_json = json.loads(res.choices[0].message.content)

In [121]:
print(result_json)

{'Service': {'Score': 6, 'Positive': {'3': 'The place is cute and the staff was very friendly. Nice menu. Good for brunch.', '8': 'I went on a Thursday morning for breakfast. Staff was attentive and the omelette was excellent.', '17': 'This place is delicious. I love the vanilla chai tea latte they have, the manager is very hands-on and really seems to really know the business.', '35': 'The manager noticed and got me my check and packed my leftovers asap.', '37': "The server couldn't have been more attentive and friendly.", '51': 'Great French press coffee and the staff is really working hard.', '60': "Fantastic meal! We didn't have to wait long and the service was spot on.", '61': "Our waitress was extremely nice and helpful. We didn't have to wait at all for Sunday brunch.", '76': 'The staff here is so welcoming and everything is very clean.', '170': 'Service was excellent. Lauryn was the best.'}, 'Negative': {'1': 'The food is good, but it takes a very long time to come out.', '2': 

In [122]:
with open("results.json", "w") as f:
    json.dump(result_json, f)

In [94]:
id2review_dict = {}
for x in data:
    id2review_dict[x['id']] = x['text']

In [95]:
categories = ["Service", "Hygiene", "Taste", "Location", "Price"]

In [123]:
def reformat_output(result_json, categories):
    ret = {}
    count = 0
    for key in result_json:
        ret[categories[count]] = {"Positive": [], "Negative": []}

        ret[categories[count]]["Positive"] = [int(k) for k in result_json[key]["Positive"].keys()]
        ret[categories[count]]["Negative"] = [int(k) for k in result_json[key]["Negative"].keys()]
        ret[categories[count]]["Score"] = float(result_json[key]["Score"])
        count += 1
    return ret
formated_output = reformat_output(result_json, categories)
print(formated_output)

{'Service': {'Positive': [3, 8, 17, 35, 37, 51, 60, 61, 76, 170], 'Negative': [1, 2, 4, 5, 6, 7, 10, 14, 15, 19, 24], 'Score': 6.0}, 'Hygiene': {'Positive': [16, 25, 26, 90, 92, 97, 99, 118, 143, 156], 'Negative': [6, 15, 20, 28, 29, 30, 32, 48, 64, 65], 'Score': 6.0}, 'Taste': {'Positive': [3, 11, 16, 17, 23, 25, 26, 49, 52, 63], 'Negative': [2, 4, 5, 10, 12, 13, 18, 28, 38, 39, 44], 'Score': 7.0}, 'Location': {'Positive': [16, 22, 23, 46, 66, 82, 85, 92, 119], 'Negative': [22, 33], 'Score': 7.0}, 'Price': {'Positive': [3, 11, 22, 26, 66, 81, 82, 92, 105, 103], 'Negative': [14, 18, 28, 33, 39, 40, 47, 68, 70, 75, 124], 'Score': 7.0}}


In [111]:
import glob
data_path = "../dataset/"
folders = ["Breakfast", "Bubble", "Burger", "Cafe", "Chinese", "Indian", "Italian" ,"Japanese", "Korean", "Mexican", "Pizza", "Vietnamese"]

count = 0
id_set = set()
files = []
for folder in folders:
    json_files = glob.glob(data_path + folder + "/*")
    ids = [f.split('/')[-1] for f in json_files]
    count += len(ids)
    for i, id in enumerate(ids):
        if id in id_set:
            print(folder, id)
            continue
        id_set.add(id)
        files.append(json_files[i])
print(count)
print(len(id_set))
print(len(files))

Burger dChRGpit9fM_kZK5pafNyA_reviews.json
Burger VCkSUsdL5P0p16DAPxVROA_reviews.json
Cafe PW5eZM5RAQEhy3wgovChhQ_reviews.json
Indian U30ggGzFpXvc2NZYwOW3qg_reviews.json
Italian PdMXmOWDRHICAx6SLgu1dQ_reviews.json
Korean EHNtEYL9GXsv1sbKChMMWw_reviews.json
Mexican afsP-p_pr4ikrboB5MtUzQ_reviews.json
Pizza cLlBDZxYJ1dt1JgMuZnXew_reviews.json
Pizza Pb5agnsD9EdCl6yuZp2jJA_reviews.json
Vietnamese Zk_GdMMPgEfKUECCxAxvwQ_reviews.json
Vietnamese FHNIvNgh3fS7VZQq2Y3dsA_reviews.json
120
109
109


In [ ]:
def query_one_json(json_file):
    with open(json_file, 'r') as f:
        data = json.load(f)
    print(json_file)
    suffix_path = '/'.join(json_file.split('/')[:-1])+'/'
    id = '_'.join(json_file.split('/')[-1].split('_')[:-1])
    new_path = suffix_path+id+'_results.json'
    if not os.path.isfile(new_path):
        res = request(data[:100])
        print(res.choices[0].message.content)
        result_json = json.loads(res.choices[0].message.content)
        formated_output = reformat_output(result_json, categories)
        with open(new_path, "w") as f:
            json.dump(formated_output, f)
for file in tqdm(files):
    try:
        query_one_json(file)
    except Exception:
        traceback.print_exc()
        

  0%|                                                                                                     | 0/109 [00:00<?, ?it/s]

../dataset/Breakfast/dChRGpit9fM_kZK5pafNyA_reviews.json
../dataset/Breakfast/PdMXmOWDRHICAx6SLgu1dQ_reviews.json


  2%|█▋                                                                                         | 2/109 [01:19<1:10:38, 39.61s/it]

{
    "Service": {
        "Score": 6.5,
        "Positive": {
            "1": "Pleasant place. Great service. Loved the salads, fresh buttery focaccacio bread sticks.",
            "3": "The waitresses and waiters are perfect the food is great the music is great I love it.",
            "5": "The service was very prompt, with great options for cappuccinos and lattes for brunch as well as creative brunch drinks.",
            "6": "Service is very friendly.",
            "10": "We greatly appreciated the service and overall had a great dining experience!",
            "13": "It was a great low key, casual spot with good vibes only!",
            "17": "Just opened this week and service was efficient, friendly and no hiccups at all.",
            "27": "Our server, Rodney, was fantastic! Never once did we feel neglected.",
            "30": "Service has also been spectacular.",
            "40": "Each entree was more delicious than the last!"
        },
        "Negative": {
          

  3%|██▌                                                                                        | 3/109 [02:28<1:31:57, 52.05s/it]

...

{
    "Service": {
        "Score": 7.5,
        "Positive": {
                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                         

 57%|██████████████████████████████████████████████████                                      | 62/109 [1:25:55<1:01:32, 78.56s/it]

{
    "Service": {
        "Score": 6.3,
        "Positive": {
             	"13": "I don't understand the low reviews on here. Maybe I just got lucky. I've ordered from here twice in the past couple months to a hotel near by. Both times the food was fast, hot, and the drivers were nice.",
            "10": "Visited this location because my nearby one was closed for the night. Though I didn't get delivery, the food was hot and better than my normal store. The toppings weren't skimpy, all my sauces were included and the whole experience was pleasant. Also, the woman working the counter was really pleasant!",
            "7": "Guess I should've read the Yelp review first. I ordered a dinner box at 12:08pm. The notification I received said my food would be delivered at 12:36. At 1pm when my food still hadn't arrived, I called the store and they assured me it would arrive in 5 minutes. The gentleman who answered was very nice. Finally, at 1:26, the driver (female) arrived. I was annoyed bu

Traceback (most recent call last):
  File "/var/folders/ph/6k474nt57bsbh53k8tc674dr0000gn/T/ipykernel_42747/976153943.py", line 17, in <module>
    query_one_json(file)
  File "/var/folders/ph/6k474nt57bsbh53k8tc674dr0000gn/T/ipykernel_42747/976153943.py", line 12, in query_one_json
    formated_output = reformat_output(result_json, categories)
  File "/var/folders/ph/6k474nt57bsbh53k8tc674dr0000gn/T/ipykernel_42747/417934570.py", line 8, in reformat_output
    ret[categories[count]]["Negative"] = [int(k) for k in result_json[key]["Negative"].keys()]
KeyError: 'Negative'
 58%|██████████████████████████████████████████████████▊                                     | 63/109 [1:27:39<1:06:00, 86.09s/it]

{
    "Service": {
        "Score": 8.5,
        "Positive": {
                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                         

In [50]:
def create_service_prompt(data):
    human_prompt = """
Given a restaurant's reviews and their IDs below, find 10 positive reviews and 10 negative reviews paraticularly regarding the services of the restaurant.
When returning the results, put the reviews that have strong opinions in the front and make sure to include the IDs of the reviews with the format below:
ID: review
========
EXAMPLE RESPONSE:
Positive reviews:
3: The service is superb!
4: The waiters are very well trained.

Negative reviews:
10: The owner's attitude is the worst!
15: The waiters need some training.

========
Reveiws:
{contents}
========
Again, return reviews that talks about the services of the restaurant.
Answer:
"""
    system_prompt = """You are a helpful assistant that finds reviews that are relevant to the restaurant's services.
"""

    reviews_str = ""
    for x in data:
        reviews_str += str(x['id']) + ": " + x['text'] + '\n'
        
    messages = [
        SystemMessagePromptTemplate.from_template(system_prompt),
        HumanMessagePromptTemplate.from_template(human_prompt),
    ]

    template = ChatPromptTemplate.from_messages(messages)
    formatted_messages = template.format_prompt(contents=reviews_str).to_messages()
    return formatted_messages
prompt = create_service_prompt(data)
print(prompt)

[SystemMessage(content="You are a helpful assistant that finds reviews that are relevant to the restaurant's services.\n"), HumanMessage(content='\nGiven a restaurant\'s reviews and their IDs below, find 10 positive reviews and 10 negative reviews regarding each of the topics listed below:\n1. Service\n2. Hygiene and environment\n3. Food quality and taste\n4. Location and transportation\n5. Price\nWhen returning the results, put the reviews that have strong opinions in the front and make sure to include the IDs of the reviews with the format below:\nID: review\n========\nEXAMPLE RESPONSE:\nPositive reviews:\n3: The service is superb!\n4: The waiters are very well trained.\n\nNegative reviews:\n10: The owner\'s attitude is the worst!\n15: The waiters need some training.\n\n========\nReveiws:\n1: If you decide to eat here, just be aware it is going to take about 2 hours from beginning to end. We have tried it multiple times, because I want to like it! I have been to it\'s other locations

In [98]:
results = chat_llm(prompt)

In [ ]:
#price, quality, transportation